In [7]:
from kafka import KafkaConsumer

In [8]:
consumer=KafkaConsumer(bootstrap_servers='localhost:9092',group_id='test1',consumer_timeout_ms=10000)
consumer.subscribe('covid_19')

In [9]:
def fill(freq,P,PP):

 P.append(0)
 PP.append(0)
 ### filling the P and PP
 i = 1
 while i <= len(freq):
  P.insert(i, P[i - 1] + freq[i - 1])
  PP.insert(i, PP[i - 1] + freq[i - 1] * freq[i - 1])
  i += 1

 return P, PP


def SqError(a, b,P,PP):
 s2 = PP[b] - PP[a - 1]
 s1 = P[b] - P[a - 1]    
 err = (s2 - (s1 * s1 / (b - a + 1)))
 return err


def approx_histogram(freq, B, delt,BestErr ):
 P, PP = fill(freq,P=[],PP=[])

 k = 1
 BestErr = [[9999999 for i in range(len(freq) + 1)] for j in range(B + 1)]
 while k <= B:
  if k == 1:
   i = 1
   while i <= len(freq):
    BestErr[k][i] = SqError(1, i,P,PP)
    i += 1

  else:
   i = 1
   while i <= len(freq):

    BestErr[k][i] = 99999999
    ini = 1;
    while ini <= k - 1:
     BestErr[k][ini] = 0.0
     ini += 1

    j =  1
    while j <= i - 1:
     if BestErr[k - 1][j] + SqError(j + 1, i,P,PP) < BestErr[k][i]:
      minm = BestErr[k - 1][j] + SqError(j + 1, i,P,PP)
      prev = BestErr[k][i - 1]
      if minm > (1 + delt) * prev:
       BestErr[k][i] = minm
      else:
       BestErr[k][i] = prev
     j += 1
    i += 1

  k += 1
 return BestErr


def buckets(bucket,errBucket):
  ### in format -> left bound,right bound,histogram error
 
  i=1
  while i<=len(errBucket)-1:
      left=i
      val=errBucket[i]
      j=i
      while j<len(errBucket)  and errBucket[j]==val:
          j+=1

      i=j
      right=j-1
      bucket.append([left,right,val])

  return bucket

In [10]:
def main(B,freq_dict,delt,new,ele,BestErr):
#     B=2  #minm no of  bucket in approx --
  val=[]
  if new in freq_dict:  #seen
     freq_dict[new]+=1
     for key in sorted(freq_dict):
      val.append(freq_dict[key])
     BestErr = approx_histogram(val, B, delt,BestErr=[])

  else: #unseen
   freq_dict[new] = 1
   in_range=False
   if new<max(ele):
    in_range=True
   else:
    in_range=False
   ele.append(new)
   ele.sort()
   for key in sorted(freq_dict):
    val.append(freq_dict[key])
   #case 1 when within the range
   if in_range:
    BestErr = approx_histogram(val, B, delt,BestErr=[])

   #case 2 when outside the range
   else:
    P, PP = fill(val,P=[],PP=[])
    buck=1
    while buck<=B:
        if buck==1:
           i=len(val)
           BestErr[buck].append(SqError(1,i,P,PP))

        else:
           i=len(val)
           BestErr[buck].insert(i, 999999)
           j =  1
           while j <= i - 1:
            if BestErr[buck - 1][j] + SqError(j + 1, i, P, PP) < BestErr[buck][i]:
             minm = BestErr[buck - 1][j] + SqError(j + 1, i, P, PP)
             prev = BestErr[buck][i - 1]
             if minm > (1 + delt) * prev:
              BestErr[buck][i] = minm
             else:
              BestErr[buck][i] = prev
            j += 1
        buck+=1

  # print("error", BestErr)
  bucket=[]
  bucket = buckets(bucket, BestErr[B])
 
  return BestErr,bucket,freq_dict

In [11]:
qi=['oxygen','cowin','ontario','covishield','covax','novavax','lockdown','hospital','sputnik','astrazeneca','covid']
ele=[1] # store the stream of elements 
freq_dict={1:4}
val=[]
BestErr=[[999999, 999999], [999999, 0.0], [999999, 0.0]]
for message in consumer:
    stri=""
    stri=stri+str(message.value)
    stri=stri.replace("b",'')
    stri=stri.replace("'",'')
    stri=str(stri.lower())
       
    if stri in qi: 
        print("new->",stri)
        index=qi.index(stri)+1              
        delt=1
        B=2
        BestErr,bucket,freq_dict=main(2,freq_dict,1,index,ele,BestErr)   
        print("frequencies-",freq_dict)                 
        print("error-", BestErr)
        print("bucket-",bucket)
        print("\n")

            

new-> oxygen
frequencies- {1: 5}
error- [[9999999, 9999999], [9999999, 0.0], [9999999, 0.0]]
bucket- [[1, 1, 0.0]]


new-> covid
frequencies- {1: 5, 11: 1}
error- [[9999999, 9999999], [9999999, 0.0, 8.0], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> oxygen
frequencies- {1: 6, 11: 1}
error- [[9999999, 9999999, 9999999], [9999999, 0.0, 12.5], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> oxygen
frequencies- {1: 7, 11: 1}
error- [[9999999, 9999999, 9999999], [9999999, 0.0, 18.0], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> oxygen
frequencies- {1: 8, 11: 1}
error- [[9999999, 9999999, 9999999], [9999999, 0.0, 24.5], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> oxygen
frequencies- {1: 9, 11: 1}
error- [[9999999, 9999999, 9999999], [9999999, 0.0, 32.0], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> covid
frequencies- {1: 9, 11: 2}
error- [[9999999, 9999999, 9999999], [9999999, 0.0, 24.5], [9999999, 0.0, 0.0]]
bucket- [[1, 2, 0.0]]


new-> oxygen
frequencies- {1: 1

error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 17484.5, 22588.666666666664, 22602.75], [9999999, 0.0, 0.0, 18.0, 2184.0]]
bucket- [[1, 2, 0.0], [3, 3, 18.0], [4, 4, 2184.0]]


new-> oxygen
frequencies- {1: 190, 11: 62, 8: 8, 7: 2}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 17672.0, 22834.666666666664, 22851.0], [9999999, 0.0, 0.0, 18.0, 2184.0]]
bucket- [[1, 2, 0.0], [3, 3, 18.0], [4, 4, 2184.0]]


new-> oxygen
frequencies- {1: 191, 11: 62, 8: 8, 7: 2}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 17860.5, 23082.0, 23100.75], [9999999, 0.0, 0.0, 18.0, 2184.0]]
bucket- [[1, 2, 0.0], [3, 3, 18.0], [4, 4, 2184.0]]


new-> oxygen
frequencies- {1: 192, 11: 62, 8: 8, 7: 2}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 18050.0, 23330.666666666664, 23352.0], [9999999, 0.0, 0.0, 18.0, 2184.0]]
bucket- [[1, 2, 0.0], [3, 3, 18.0], [4, 4, 2184.0]]


new-> oxygen
frequencies- {1: 193, 11: 62, 8: 8, 7: 

error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 57800.0, 74654.0, 74681.0], [9999999, 0.0, 0.0, 60.5, 7480.666666666667]]
bucket- [[1, 2, 0.0], [3, 3, 60.5], [4, 4, 7480.666666666667]]


new-> covid
frequencies- {1: 344, 11: 116, 8: 15, 7: 4}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 57800.0, 74654.0, 74672.75], [9999999, 0.0, 0.0, 60.5, 7622.0]]
bucket- [[1, 2, 0.0], [3, 3, 60.5], [4, 4, 7622.0]]


new-> covid
frequencies- {1: 344, 11: 117, 8: 15, 7: 4}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 57800.0, 74654.0, 74666.0], [9999999, 0.0, 0.0, 60.5, 7764.666666666667]]
bucket- [[1, 2, 0.0], [3, 3, 60.5], [4, 4, 7764.666666666667]]


new-> oxygen
frequencies- {1: 345, 11: 117, 8: 15, 7: 4}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 58140.5, 75100.66666666666, 75114.75], [9999999, 0.0, 0.0, 60.5, 7764.666666666667]]
bucket- [[1, 2, 0.0], [3, 3, 60.5], [4, 4, 7764.666666666667]]


new->

new-> oxygen
frequencies- {1: 526, 11: 178, 8: 22, 7: 7}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 134680.5, 174534.0, 174570.75], [9999999, 0.0, 0.0, 112.5, 17934.0]]
bucket- [[1, 2, 0.0], [3, 3, 112.5], [4, 4, 17934.0]]


new-> oxygen
frequencies- {1: 527, 11: 178, 8: 22, 7: 7}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 135200.0, 175216.6666666667, 175257.0], [9999999, 0.0, 0.0, 112.5, 17934.0]]
bucket- [[1, 2, 0.0], [3, 3, 112.5], [4, 4, 17934.0]]


new-> oxygen
frequencies- {1: 528, 11: 178, 8: 22, 7: 7}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 135720.5, 175900.6666666667, 175944.75], [9999999, 0.0, 0.0, 112.5, 17934.0]]
bucket- [[1, 2, 0.0], [3, 3, 112.5], [4, 4, 17934.0]]


new-> covid
frequencies- {1: 528, 11: 179, 8: 22, 7: 7}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 135720.5, 175900.6666666667, 175934.0], [9999999, 0.0, 0.0, 112.5, 18152.666666666664]]
bucket- [[1, 

error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 219122.0, 284018.0, 284066.0], [9999999, 0.0, 0.0, 180.5, 29440.666666666668]]
bucket- [[1, 2, 0.0], [3, 3, 180.5], [4, 4, 29440.666666666668]]


new-> oxygen
frequencies- {1: 672, 11: 228, 8: 28, 7: 9}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 219784.5, 284888.6666666666, 284940.75], [9999999, 0.0, 0.0, 180.5, 29440.666666666668]]
bucket- [[1, 2, 0.0], [3, 3, 180.5], [4, 4, 29440.666666666668]]


new-> covid
frequencies- {1: 672, 11: 229, 8: 28, 7: 9}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 219784.5, 284888.6666666666, 284929.0], [9999999, 0.0, 0.0, 180.5, 29720.666666666668]]
bucket- [[1, 2, 0.0], [3, 3, 180.5], [4, 4, 29720.666666666668]]


new-> oxygen
frequencies- {1: 673, 11: 229, 8: 28, 7: 9}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 220448.0, 285760.6666666666, 285804.75], [9999999, 0.0, 0.0, 180.5, 29720.666666666668]]
buck

...

new-> oxygen
frequencies- {1: 12749, 11: 4464, 8: 531, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80175784.5, 103276372.66666666, 103276429.0], [9999999, 0.0, 0.0, 99012.5, 11611132.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 99012.5], [4, 4, 11611132.666666666]]


new-> oxygen
frequencies- {1: 12750, 11: 4464, 8: 531, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80188448.0, 103292960.66666666, 103293012.75], [9999999, 0.0, 0.0, 99012.5, 11611132.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 99012.5], [4, 4, 11611132.666666666]]


new-> oxygen
frequencies- {1: 12751, 11: 4464, 8: 531, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80201112.5, 103309550.0, 103309598.0], [9999999, 0.0, 0.0, 99012.5, 11611132.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 99012.5], [4, 4, 11611132.666666666]]


new-> covid
frequencies- {1: 12751, 11: 4465, 8: 531, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999],


new-> covid
frequencies- {1: 12805, 11: 4482, 8: 534, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80886480.5, 104183702.0, 104183738.75], [9999999, 0.0, 0.0, 100352.0, 11704074.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 100352.0], [4, 4, 11704074.666666666]]


new-> oxygen
frequencies- {1: 12806, 11: 4482, 8: 534, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80899200.0, 104200362.66666666, 104200396.0], [9999999, 0.0, 0.0, 100352.0, 11704074.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 100352.0], [4, 4, 11704074.666666666]]


new-> oxygen
frequencies- {1: 12807, 11: 4482, 8: 534, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 80911920.5, 104217024.66666666, 104217054.75], [9999999, 0.0, 0.0, 100352.0, 11704074.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 100352.0], [4, 4, 11704074.666666666]]


new-> oxygen
frequencies- {1: 12808, 11: 4482, 8: 534, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9

new-> oxygen
frequencies- {1: 12870, 11: 4502, 8: 536, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81715328.0, 105253570.66666666, 105253587.0], [9999999, 0.0, 0.0, 101250.0, 11810904.0]]
bucket- [[1, 2, 0.0], [3, 3, 101250.0], [4, 4, 11810904.0]]


new-> oxygen
frequencies- {1: 12871, 11: 4502, 8: 536, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81728112.5, 105270316.66666666, 105270330.75], [9999999, 0.0, 0.0, 101250.0, 11810904.0]]
bucket- [[1, 2, 0.0], [3, 3, 101250.0], [4, 4, 11810904.0]]


new-> oxygen
frequencies- {1: 12872, 11: 4502, 8: 536, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81740898.0, 105287064.0, 105287076.0], [9999999, 0.0, 0.0, 101250.0, 11810904.0]]
bucket- [[1, 2, 0.0], [3, 3, 101250.0], [4, 4, 11810904.0]]


new-> covid
frequencies- {1: 12872, 11: 4503, 8: 536, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81740898.0, 105287064.0, 1

error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81945602.0, 105547268.66666666, 105547348.75], [9999999, 0.0, 0.0, 101700.5, 11875704.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 101700.5], [4, 4, 11875704.666666666]]


new-> oxygen
frequencies- {1: 12889, 11: 4514, 8: 537, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81958404.5, 105564038.0, 105564113.0], [9999999, 0.0, 0.0, 101700.5, 11875704.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 101700.5], [4, 4, 11875704.666666666]]


new-> oxygen
frequencies- {1: 12890, 11: 4514, 8: 537, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81971208.0, 105580808.66666666, 105580878.75], [9999999, 0.0, 0.0, 101700.5, 11875704.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 101700.5], [4, 4, 11875704.666666666]]


new-> oxygen
frequencies- {1: 12891, 11: 4514, 8: 537, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 81984012.5, 105597580.66666666, 105597

new-> oxygen
frequencies- {1: 12953, 11: 4532, 8: 540, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 82779844.5, 106616124.66666666, 106616148.75], [9999999, 0.0, 0.0, 103058.0, 11969698.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 103058.0], [4, 4, 11969698.666666666]]


new-> covid
frequencies- {1: 12953, 11: 4533, 8: 540, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 82779844.5, 106616124.66666666, 106616158.0], [9999999, 0.0, 0.0, 103058.0, 11975324.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 103058.0], [4, 4, 11975324.666666666]]


new-> oxygen
frequencies- {1: 12954, 11: 4533, 8: 540, 7: 86}
error- [[9999999, 9999999, 9999999, 9999999, 9999999], [9999999, 0.0, 82792712.0, 106632978.66666666, 106633008.75], [9999999, 0.0, 0.0, 103058.0, 11975324.666666666]]
bucket- [[1, 2, 0.0], [3, 3, 103058.0], [4, 4, 11975324.666666666]]


new-> covid
frequencies- {1: 12954, 11: 4534, 8: 540, 7: 86}
error- [[9999999, 9999999, 9999999, 99999

In [6]:
consumer.close()